In [ ]:
import json

In [ ]:
with open('/content/training.json') as f:
  train_data = json.load(f)

In [ ]:
with open('/content/test.json') as f:
  test_data = json.load(f)

In [ ]:
def calculate_area(entry):
    min_r = entry['minimum']['r']
    min_c = entry['minimum']['c']
    max_r = entry['maximum']['r']
    max_c = entry['maximum']['c']
    area = (max_r - min_r) * (max_c - min_c)
    return area

In [ ]:
count = 0
for image in train_data:
  for item in image['objects']:
    area = calculate_area(item['bounding_box'])
    item['area'] = area
    if item['category'] == 'red blood cell' or item['category'] == 'leukocyte':
      #not infected
      item['diagnosis'] = 0
    else:
      #infected
      item['diagnosis'] = 1

In [ ]:
for image in test_data:
  for item in image['objects']:
    area = calculate_area(item['bounding_box'])
    item['area'] = area
    if item['category'] == 'red blood cell' or item['category'] == 'leukocyte':
      item['diagnosis'] = 0
    else:
      item['diagnosis'] = 1

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

In [ ]:
official_train = {}
data = pd.DataFrame(train_data)
data = data['objects']
#data = data[:80]
count = 0
for i in range(len(data)):
  for j in range(len(data[i])):
    official_train[count] = {}
    area = data[i][j]['area']
    official_train[count]["area"] = area
    diagnosis = data[i][j]['diagnosis']
    official_train[count]["diagnosis"] = diagnosis
    count += 1

In [ ]:
print(len(official_train))

80113


In [ ]:
official_test = {}
data = pd.DataFrame(test_data)
data = data['objects']
#data = data[:20]
count = 0
for i in range(len(data)):
  for j in range(len(data[i])):
    official_test[count] = {}
    area = data[i][j]['area']
    official_test[count]["area"] = area
    diagnosis = data[i][j]['diagnosis']
    official_test[count]["diagnosis"] = diagnosis
    count += 1

In [ ]:
train_df = pd.DataFrame.from_dict(official_train, orient = 'index')
test_df = pd.DataFrame.from_dict(official_test, orient = 'index')

In [ ]:
X = train_df[['area']]
y = train_df[['diagnosis']]

In [ ]:
X_test = test_df[['area']]
y_test = test_df[['diagnosis']]

In [ ]:
model = LogisticRegression()
model.fit(X, y)

/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


LogisticRegression()

In [ ]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.metrics import roc_auc_score

In [ ]:
y_pred = model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

In [ ]:
y_scores = model.predict_proba(X_test)[:, 1]

# Compute the ROC AUC score
roc_auc = roc_auc_score(y_test, y_scores)

print(f"ROC AUC Score: {roc_auc:.2f}")

ROC AUC Score: 0.80


In [ ]:
print(f'Accuracy: {accuracy * 100:.2f}%')
print(f'Precision: {precision * 100:.2f}%')
print(f'Recall: {recall * 100:.2f}%')
print(f'F1 Score: {f1 * 100:.2f}%')

Accuracy: 65.70%
Precision: 10.75%
Recall: 76.62%
F1 Score: 18.86%
